**QUESTION 1**


In [0]:
# Import required libraries

from graphframes import *
from graphframes import GraphFrame
from pyspark.sql import SparkSession


In [0]:
# Load the data into a DataFrame
df = spark.read.option("header", "true").csv("dbfs:/FileStore/T_T100D_SEGMENT_US_CARRIER_ONLY_with_optional-1.csv")

# Create vertices DataFrame. Here, vertices should be the airports. So we use origin which represents the airports
vertices = df.select("ORIGIN", "ORIGIN_CITY_NAME").distinct()
vertices = vertices.withColumnRenamed("ORIGIN", "id").withColumnRenamed("ORIGIN_CITY_NAME", "name")

# Create edges DataFrame. Here we use the destination as the edge because it represents the connection between the vertices (airport) => represents flights between the airports
edges = df.select("ORIGIN", "DEST")
edges = edges.withColumnRenamed("ORIGIN", "src").withColumnRenamed("DEST", "dst")

# Create GraphFrame with the created vertices and edges
g = GraphFrame(vertices, edges)


In [0]:
g.vertices.show()

+---+--------------------+
| id|                name|
+---+--------------------+
|ABQ|     Albuquerque, NM|
|AEX|      Alexandria, LA|
|ABL|          Ambler, AK|
|ACT|            Waco, TX|
|ADK|     Adak Island, AK|
|6AK|          Newtok, AK|
|ADS|          Dallas, TX|
|ABR|        Aberdeen, SD|
|A27|      Pogo Mines, AK|
|ACV|   Arcata/Eureka, CA|
|ABE|Allentown/Bethleh...|
|AAF|    Apalachicola, FL|
|AET|       Allakaket, AK|
|ABY|          Albany, GA|
|ADQ|          Kodiak, AK|
|1G4|   Peach Springs, AZ|
|ACY|   Atlantic City, NJ|
|7AK|            Akun, AK|
|ACK|       Nantucket, MA|
|ABI|         Abilene, TX|
+---+--------------------+
only showing top 20 rows



In [0]:
g.edges.show()

+---+---+
|src|dst|
+---+---+
|1G4|1G4|
|1G4|BLD|
|1G4|BLD|
|1NY|BED|
|6AK|BET|
|6AK|WWT|
|7AK|CDB|
|7AK|DUT|
|7AK|DUT|
|7AK|KQA|
|7AK|KQA|
|A27|FAI|
|AAF|OCF|
|ABE|AFW|
|ABE|ATL|
|ABE|AVP|
|ABE|BDR|
|ABE|BNA|
|ABE|CLT|
|ABE|CLT|
+---+---+
only showing top 20 rows



**a) Top 5 nodes with the highest outdegree and the count of the number of outgoing edges in each**

ORD (Chicago O'Hare Intl Airport) has the highest outdegree => it is highly connected and has a large number of direct flights departing to various destinations. Similar inferences can be made for the rest (DENver Intl Airport, ATLanta Intl Airport, Dallas/FortWorth Intl Airport, IAH: George Bush Intercontinental Airport in Houston, TX)

In [0]:
# Calculate outdegrees using the graphframes library
outdeg = g.outDegrees

# Find top 5 nodes with the highest outdegree and display count of each
top_outdeg = outdeg.orderBy('outDegree', ascending=False).limit(5)

# Display the results
top_outdeg.show()


+---+---------+
| id|outDegree|
+---+---------+
|ORD|     1266|
|DEN|     1105|
|ATL|      962|
|DFW|      875|
|IAH|      697|
+---+---------+



**b) Top 5 nodes with the highest indegree and the count of the number of incoming edges in each**

ORD (Chicago O'Hare Intl Airport) has the highest indegree => it is highly connected and has a large number of direct flights arriving from various destinations. Similar inferences can be made for the rest (DENver Intl Airport, ATLanta Intl Airport, Dallas/FortWorth Intl Airport, IAH: George Bush Intercontinental Airport in Houston, TX). Notice that these airports were also the ones with highest outdegrees implying that these airports probbaly handle a high volume of both arrivals and departures and could be connecting different regions.

In [0]:
# Calculate indegrees using the graphframes library
indeg = g.inDegrees

# Find top 5 nodes with the highest indegree and display count of each
top_indeg = indeg.orderBy('inDegree', ascending=False).limit(5)

# Display the results
top_indeg.show()


+---+--------+
| id|inDegree|
+---+--------+
|ORD|    1267|
|DEN|    1098|
|ATL|     965|
|DFW|     879|
|IAH|     712|
+---+--------+



**c) Calculation of PageRank for each of the nodes and output the top 5 nodes with the highest PageRank values**

We see that the top 4 nodes are same as the results obtained for indegrees and outdegrees above indicating that these airports could be very important and influential with many incoming and outgoing connections. Despite ANC (Alaska) having low indegrees and outdegrees compared to the rest of the airports on our list, it may have a higher pagerank than IAH because of the quality of connections or its position in the network of airports. IAH may not have the same influence as ANC and this could be the reason why it has lower pagerank than ANC. If we display the top 10 nodes we, see that IAH is not far behind on the pagerank list (top 9th) and the value is also very close to ANC.


In [0]:
# Calculate PageRank with resetProb = 0.15 (15% chance that a random internet surfer will jump to a random node instead of following a link) and tolerance = 0.01 (stop iterating when the change in values of pagerank between iteration is < 0.01)
pg_r = g.pageRank(resetProbability=0.15, tol=0.01)

# Find top 5 nodes with the highest PageRank values
top_pg_r = pg_r.vertices.orderBy('pagerank', ascending=False).limit(5)

# Show the result
top_pg_r.show()

+---+--------------------+------------------+
| id|                name|          pagerank|
+---+--------------------+------------------+
|ORD|         Chicago, IL|19.542944816964106|
|DEN|          Denver, CO|18.123234208092107|
|ATL|         Atlanta, GA|14.365696396005108|
|DFW|Dallas/Fort Worth...|14.036839277723828|
|ANC|       Anchorage, AK|11.940414424514335|
+---+--------------------+------------------+



In [0]:
# Find top 10 nodes with the highest PageRank values
top_pg_r10 = pg_r.vertices.orderBy('pagerank', ascending=False).limit(10)

# Show the result
top_pg_r10.show()

+---+--------------------+------------------+
| id|                name|          pagerank|
+---+--------------------+------------------+
|ORD|         Chicago, IL|19.542944816964106|
|DEN|          Denver, CO|18.123234208092107|
|ATL|         Atlanta, GA|14.365696396005108|
|DFW|Dallas/Fort Worth...|14.036839277723828|
|ANC|       Anchorage, AK|11.940414424514335|
|PHX|         Phoenix, AZ| 11.40992939916564|
|BET|          Bethel, AK| 11.31216649757965|
|SEA|         Seattle, WA|10.620334485874292|
|IAH|         Houston, TX|10.370943908067842|
|LAS|       Las Vegas, NV|10.344745141714421|
+---+--------------------+------------------+



**d) Strongly connected components algorithm tofind the top 5 components with the largest number of nodes.**

Component 0 is the largest strongly connected component with 760 nodes. This means that a large portion of the airport network in January, 2025 was highly interconnected with many airports having direct or indirect connections to each other. The rest of the components have realtively smaller nodes implying that a small subgraph where these airports are mutually reachable.

In [0]:

# Run Strongly Connected Components algorithm from the graphframes library
scc = g.stronglyConnectedComponents(maxIter=10)

# Count the number of nodes in each strongly connected component
scc_counts = scc.groupBy("component").count()

# Find top 5 components with the largest number of nodes and display them
top_scc = scc_counts.orderBy("count", ascending=False).limit(5)
top_scc.show()

+------------+-----+
|   component|count|
+------------+-----+
|           0|  760|
|523986010114|    3|
|154618822658|    2|
|300647710721|    2|
|163208757249|    2|
+------------+-----+



If we want to take a deeper look into which airports contribute to the resulst obtained above, we look at the airport ids. A lot of airports like AFW (Fortworth Alliance Airport), COS (Colorado Springs Airport), etc. are part of the largest strongly connected component indicating that these airports have stong mutual connectivity with other airports. Component 163208757249 has 2 strongly connected components which implies that this small size suggests connetions between 2 airports. LEE airport is located in Maryland which is the ninth smallest state in the US; which could be the reason why it has a very few strongly connected components.

In [0]:
# Display the top 5 components with their node IDs to see which airports are stongly connected and display the result
top_scc_ids = scc.join(top_scc, "component").select("component", "id", "count")
display(top_scc_ids)

component id count 0 AFW 760 0 COS 760 0 HNM 760 0 SDF 760 0 TKF 760 0 TOG 760 0 CLL 760 0 PIR 760 0 CMI 760 0 EVV 760 0 GTR 760 0 MSN 760 0 PTU 760 0 CON 760 0 FLO 760 0 OPF 760 0 RIC 760 0 STX 760 0 DCA 760 0 CKB 760 0 GUM 760 0 HCR 760 0 IPL 760 0 LNY 760 0 MBL 760 0 APF 760 0 HRO 760 0 NEW 760 0 PGV 760 0 RBG 760 0 CDR 760 0 CFT 760 0 GRI 760 0 HII 760 0 KPN 760 0 FOD 760 0 FVO 760 0 ITO 760 0 MPB 760 0 IAG 760 0 NUI 760 0 TN8 760 0 HHH 760 0 INT 760 0 MRK 760 0 MSP 760 0 AOO 760 0 AVL 760 0 CHS 760 0 KLL 760 0 MXY 760 0 IWD 760 0 MYR 760 0 PIT 760 0 SLK 760 0 CPX 760 0 GST 760 0 IGG 760 0 MCK 760 0 SXQ 760 0 DSM 760 0 KEK 760 0 LEB 760 0 SJT 760 0 SLC 760 0 DVL 760 0 PWK 760 0 CYS 760 0 DEN 760 0 IAB 760 0 VQS 760 0 AKI 760 0 KAL 760 0 OGD 760 0 SGF 760 0 COD 760 0 INL 760 0 MYU 760 0 PGA 760 0 PVU 760 0 DTO 760 0 PTH 760 0 AZ3 760 0 CEM 760 0 KLW 760 0 KTS 760 163208757249 LEE 2 0 MDW 760 0 CHO 760 0 CHU 760 0 CKD 760 0 DAY 760 0 LGC 760 0 LMA 760 0 TKJ 760 0 BTM 760 0 LUK 760 0 BWI 760 0 ABQ 760 0 MHK 760 0 MSL 760 0 RSH 760 0 NUP 760 0 SMF 760 0 SNA 760 0 AEX 760 0 APC 760 0 GPT 760 0 NPT 760 0 OME 760 0 ABL 760 0 GRB 760 0 HMN 760 0 ACT 760 0 HLN 760 0 MEM 760 0 YUM 760 0 DRG 760 0 ADK 760 0 LUP 760 0 CEF 760 0 6AK 760 0 AKB 760 0 DTW 760 0 FAR 760 0 KLG 760 0 OLF 760 0 SCK 760 0 HDN 760 0 SHV 760 0 BMI 760 0 MWA 760 0 SDP 760 0 BJI 760 0 ORH 760 0 PSE 760 0 SEE 760 0 BTT 760 0 PWM 760 0 ADS 760 0 ALS 760 0 CXF 760 0 GAI 760 0 OOK 760 0 RDU 760 0 SBA 760 0 SCF 760 0 TUP 760 0 WNA 760 0 CKX 760 0 EKO 760 0 FRD 760 0 KCQ 760 0 LAX 760 0 LYH 760 0 PIA 760 0 RHI 760 0 TIX 760 0 HKY 760 0 JLN 760 0 GRK 760 0 AXX 760 0 DFW 760 0 EUG 760 0 FRG 760 0 ORF 760 0 ANC 760 0 ONP 760 0 SVC 760 0 CNO 760 0 CVN 760 0 NCN 760 0 SYR 760 0 IKO 760 0 KAE 760 0 KBC 760 0 RDB 760 0 BLD 760 0 CNY 760 0 EGE 760 0 MTH 760 0 BIF 760 0 FAI 760 0 SOV 760 0 ELV 760 0 HTO 760 0 JZT 760 0 MYK 760 0 UTO 760 0 ABR 760 0 BVU 760 0 GLV 760 0 IND 760 0 KTN 760 0 SAD 760 0 AUS 760 0 FOK 760 0 WTK 760 0 XWA 760 0 WRI 760 0 BFI 760 0 CCR 760 0 FYU 760 0 KNW 760 0 LBF 760 0 LWM 760 0 MOU 760 0 A27 760 0 EAA 760 0 FMN 760 0 MHT 760 0 GGG 760 0 KEB 760 0 ORV 760 0 PUB 760 0 XNA 760 0 KKH 760 0 SFB 760 0 SMX 760 0 UKI 760 0 LNS 760 0 RNO 760 0 ELP 760 0 PLN 760 0 DRO 760 0 MKK 760 0 OWB 760 0 PUW 760 0 BJC 760 0 DOV 760 0 HNL 760 0 NYL 760 0 WLK 760 0 BCB 760 0 HIO 760 0 AIA 760 0 ISP 760 0 LPS 760 0 MTN 760 0 VNC 760 0 EGX 760 0 MFE 760 0 SWO 760 0 USA 760 0 AKP 760 0 ART 760 0 BGM 760 163208757249 FXE 2 0 IFP 760 0 OGS 760 0 CMX 760 0 GCC 760 0 GEG 760 0 PIB 760 0 TSM 760 0 ACV 760 0 BKW 760 0 BLV 760 0 PTK 760 0 PVC 760 0 RSW 760 0 ABE 760 0 LIH 760 0 MCO 760 0 STL 760 0 AGN 760 0 ILI 760 0 IMT 760 0 TNC 760 0 ASE 760 154618822658 LNA 2 0 AIN 760 0 AMA 760 0 BOI 760 0 BWG 760 0 GLH 760 0 SKK 760 0 TPA 760 0 UIN 760 0 ALO 760 0 LAR 760 0 LWS 760 0 TAL 760 0 BRW 760 0 RKS 760 0 YKM 760 0 SPN 760 0 VLD 760 0 COU 760 0 LBL 760 0 PQI 760 0 TEX 760 0 BRL 760 0 BMG 760 0 TTN 760 0 TWF 760 0 CSG 760 0 KSM 760 0 RDM 760 0 CVO 760 0 GCN 760 0 HKB 760 0 PAM 760 0 PSK 760 0 TSS 760 0 TUL 760 0 CIK 760 0 HHR 760 0 MLB 760 0 OTZ 760 0 OWD 760 0 CEZ 760 0 OKC 760 0 SGY 760 0 DAB 760 0 MEI 760 154618822658 OCF 2 0 PGM 760 523986010114 TIW 3 0 DBQ 760 0 DIO 760 0 EAR 760 0 EMK 760 0 GBH 760 0 GDC 760 0 KMO 760 0 TEB 760 0 AHN 760 0 JBR 760 0 RAP 760 0 HOU 760 0 PML 760 0 SIT 760 0 BGR 760 0 CZN 760 0 MIE 760 0 MQY 760 0 OMA 760 0 SHR 760 0 IAD 760 0 IRK 760 0 BED 760 0 LCK 760 0 LRU 760 0 NME 760 0 SJC 760 0 WBQ 760 0 KVC 760 0 MCG 760 0 ATL 760 0 CAK 760 0 LGB 760 0 T8X 760 0 CWA 760 0 RST 760 0 UGN 760 0 VCT 760 0 WAA 760 0 ENA 760 0 GUP 760 0 ROW 760 0 ILG 760 0 LAF 760 0 OBU 760 0 PPG 760 0 RMP 760 0 CHA 760 0 IAN 760 0 LGA 760 0 VPS 760 0 APN 760 0 BQK 760 0 RBY 760 0 BIS 760 0 C01 760 0 JFK 760 0 SOW 760 0 SVA 760 0 BTI 760 0 MCW 760 0 SFO 760 0 BFD 760 0 GUC 760 0 SQL 760 0 AET 760 0 BRO 760 0 SUA 760 0 UOX 760 0 GNU 760 0 MSY 760 0 SBY 760 0 CRW 760 0 XXP 760 0 BFL 

**e)  Triangle counts algorithm on each of the vertices and output the top 5 vertices with the largest triangle count.**

DFW has the highest triangle counts of 3481 followed by ORD, ATL, DEN, and LAS. Therfore, we can conclude that DFW is part of 3,481 such triangles (three airports where each airport has flights to the other two) and similar conclusions can be made for the other airports on the list. Therefore, these airports have lots of flights connecting it to other airports that help travellers reach many different desired destinations.

In [0]:

# Run Triangle Count algorithm using the graphframes library
tc = g.triangleCount()

# Find top 5 vertices with the largest triangle count and display the results
top_tc = tc.orderBy('count', ascending=False).limit(5)
top_tc.show()



+-----+---+--------------------+
|count| id|                name|
+-----+---+--------------------+
| 3481|DFW|Dallas/Fort Worth...|
| 3325|ORD|         Chicago, IL|
| 3303|ATL|         Atlanta, GA|
| 3246|DEN|          Denver, CO|
| 2937|LAS|       Las Vegas, NV|
+-----+---+--------------------+



**QUESTION 2**


In [0]:
# loading the dataset and converting it into a dataframe
tweets = spark.read.csv("dbfs:/FileStore/Tweets.csv", header=True, inferSchema=True)

# filter/drop the rows that have null as text column
tweets_clean = tweets.filter(tweets.text.isNotNull())


In [0]:
display(tweets_clean)

tweet_id airline_sentiment airline_sentiment_confidence negativereason negativereason_confidence airline airline_sentiment_gold name negativereason_gold retweet_count text tweet_coord tweet_created tweet_location user_timezone 570306133677760513 neutral 1.0 null null Virgin America null cairdin null 0 @VirginAmerica What @dhepburn said. null 2015-02-24 11:35:52 -0800 null Eastern Time (US & Canada) 570301130888122368 positive 0.3486 null 0.0 Virgin America null jnardino null 0 @VirginAmerica plus you've added commercials to the experience... tacky. null 2015-02-24 11:15:59 -0800 null Pacific Time (US & Canada) 570301083672813571 neutral 0.6837 null null Virgin America null yvonnalynn null 0 @VirginAmerica I didn't today... Must mean I need to take another trip! null 2015-02-24 11:15:48 -0800 Lets Play Central Time (US & Canada) 570301031407624196 negative 1.0 Bad Flight 0.7033 Virgin America null jnardino null 0 "@VirginAmerica it's really aggressive to blast obnoxious ""entertainment"" in your guests' faces & they have little recourse" null 2015-02-24 11:15:36 -0800 null Pacific Time (US & Canada) 570300817074462722 negative 1.0 Can't Tell 1.0 Virgin America null jnardino null 0 @VirginAmerica and it's a really big bad thing about it null 2015-02-24 11:14:45 -0800 null Pacific Time (US & Canada) 570300767074181121 negative 1.0 Can't Tell 0.6842 Virgin America null jnardino null 0 @VirginAmerica seriously would pay $30 a flight for seats that didn't have this playing.
 null null null null 570300616901320704 positive 0.6745 null 0.0 Virgin America null cjmcginnis null 0 @VirginAmerica yes, nearly every time I fly VX this “ear worm” won’t go away :) null 2015-02-24 11:13:57 -0800 San Francisco CA Pacific Time (US & Canada) 570300248553349120 neutral 0.634 null null Virgin America null pilot null 0 @VirginAmerica Really missed a prime opportunity for Men Without Hats parody, there. https://t.co/mWpG7grEZP null 2015-02-24 11:12:29 -0800 Los Angeles Pacific Time (US & Canada) 570299953286942721 positive 0.6559 null null Virgin America null dhepburn null 0 @virginamerica Well, I didn't…but NOW I DO! :-D null 2015-02-24 11:11:19 -0800 San Diego Pacific Time (US & Canada) 570295459631263746 positive 1.0 null null Virgin America null YupitsTate null 0 @VirginAmerica it was amazing, and arrived an hour early. You're too good to me. null 2015-02-24 10:53:27 -0800 Los Angeles Eastern Time (US & Canada) 570294189143031808 neutral 0.6769 null 0.0 Virgin America null idk_but_youtube null 0 @VirginAmerica did you know that suicide is the second leading cause of death among teens 10-24 null 2015-02-24 10:48:24 -0800 1/1 loner squad Eastern Time (US & Canada) 570289724453216256 positive 1.0 null null Virgin America null HyperCamiLax null 0 @VirginAmerica I <3 pretty graphics. so much better than minimal iconography. :D null 2015-02-24 10:30:40 -0800 NYC America/New_York 570289584061480960 positive 1.0 null null Virgin America null HyperCamiLax null 0 @VirginAmerica This is such a great deal! Already thinking about my 2nd trip to @Australia & I haven't even gone on my 1st trip yet! ;p null 2015-02-24 10:30:06 -0800 NYC America/New_York 570287408438120448 positive 0.6451 null null Virgin America null mollanderson null 0 @VirginAmerica @virginmedia I'm flying your #fabulous #Seductive skies again! U take all the #stress away from travel http://t.co/ahlXHhKiyn null 2015-02-24 10:21:28 -0800 null Eastern Time (US & Canada) 570285904809598977 positive 1.0 null null Virgin America null sjespers null 0 @VirginAmerica Thanks! null 2015-02-24 10:15:29 -0800 San Francisco, CA Pacific Time (US & Canada) 570282469121007616 negative 0.6842 Late Flight 0.3684 Virgin America null smartwatermelon null 0 @VirginAmerica SFO-PDX schedule is still MIA. null 2015-02-24 10:01:50 -0800 palo alto, ca Pacific Time (US & Canada) 570277724385734656 positive 1.0 null null Virgin America null ItzBrianHunty null 0 @VirginAmerica So excited for my first cross country flight L

In [0]:
# import all the necessary libraries - tokenizer, stop words removed, hasher
from pyspark.ml.feature import Tokenizer, StopWordsRemover, HashingTF, StringIndexer
from pyspark.ml import Pipeline

# Split (tokenize) the input (text col) and output the tokenized text
tokenizer = Tokenizer(inputCol="text", outputCol="words")

# Stop Word Removal: Removing common stop-words using the lib provided
stopwords_remover = StopWordsRemover(inputCol="words", outputCol="filtered_words")

# Term Hashing: Converting words into term-frequency vectors based on the input col
hashing_tf = HashingTF(inputCol="filtered_words", outputCol="features")

# Label Conversion: Mapping sentiment labels to numerical values for ease 
label_indexer = StringIndexer(inputCol="airline_sentiment", outputCol="label")

# Creating the pipeline with all transformations - tokenizer, stopwords remover, hasher, and label indexer
pipeline = Pipeline(stages=[tokenizer, stopwords_remover, hashing_tf, label_indexer])


In [0]:
# fit the above created pipeline to the cleaned tweet data set (apply transformations to the dataset together instead of doing it individually)
processed_tweets = pipeline.fit(tweets_clean).transform(tweets_clean)


In [0]:
from pyspark.ml.classification import LogisticRegression
from pyspark.ml.tuning import ParamGridBuilder, CrossValidator
from pyspark.ml.evaluation import MulticlassClassificationEvaluator

# Split the transformed data into training and testing set for evaluation. Fix the seed for reproducibility
train_data, test_data = processed_tweets.randomSplit([0.8, 0.2], seed=2)

# Define the logistic regression model
lr = LogisticRegression(featuresCol="features", labelCol="label")

# Define a parameter grid for tuning
param_grid = ParamGridBuilder().addGrid(lr.regParam, [0.1, 0.01]).build()



# Define a cross validator (with 3 folds) for model selection
cross_val = CrossValidator(estimator=lr, estimatorParamMaps=param_grid, evaluator=MulticlassClassificationEvaluator(), numFolds=3)

# Train model using cross-validation on training data
cv_model = cross_val.fit(train_data)

# Make predictions on the testing set using the training model
predictions = cv_model.transform(test_data)

# Define the evaluator
evaluator = MulticlassClassificationEvaluator(labelCol="label", predictionCol="prediction")

# Calculat eht accuracy of the mabove model
accuracy = evaluator.setMetricName("accuracy").evaluate(predictions)

# Calculate other metrics like precision, recall and f1 score that are important classification metrics
precision = evaluator.setMetricName("weightedPrecision").evaluate(predictions)
recall = evaluator.setMetricName("weightedRecall").evaluate(predictions)
f1 = evaluator.setMetricName("f1").evaluate(predictions)

# Print evaluation metrics
print(f"Accuracy: {accuracy:.4f}")
print(f"Weighted Precision: {precision:.4f}")
print(f"Weighted Recall: {recall:.4f}")
print(f"F1 Score: {f1:.4f}")


Accuracy: 0.7305
Weighted Precision: 0.7168
Weighted Recall: 0.7305
F1 Score: 0.7198


In [0]:
from pyspark.sql.functions import col

# Cast label and prediction columns to integer 
predictions = predictions.withColumn("label", col("label").cast("int"))
predictions = predictions.withColumn("prediction", col("prediction").cast("int"))

# Pivot the counts to get a matrix-like format
confusion_df = predictions.groupBy("label").pivot("prediction").count().na.fill(0).orderBy("label")

# Show the confusion metrics
confusion_df.show()


+-----+----+---+---+
|label|   0|  1|  2|
+-----+----+---+---+
|    0|1582|169| 46|
|    1| 286|267| 64|
|    2| 134| 71|238|
+-----+----+---+---+

